## 1 환경설정

In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container {width:80% !important;}</style>"))
%matplotlib inline

import pandas as pd
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
from scipy import stats
import warnings
import folium
import folium.plugins
import requests
import json
import folium.plugins
from IPython.display import Image
warnings.filterwarnings('ignore')

mpl.rcParams['figure.figsize'] = (12,8)  #시각화 figure default 설정
mpl.rcParams['font.family'] = 'NanumGothic' #폰트 디폴트 설정
mpl.rcParams['font.size'] = 10    #폰트 사이즈 디폴트 설정
plt.rcParams['axes.unicode_minus'] = False
%config InlineBackend.figure_format='retina' # 그래프 글씨 뚜렷
pd.options.display.float_format = '{:.3f}'.format # 넘파이 과학적 표기 제거

In [2]:
# 부산 행정구역 json raw파일(githubcontent)
r = requests.get('https://raw.githubusercontent.com/raqoon886/Local_HangJeongDong/master/hangjeongdong_%EB%B6%80%EC%82%B0%EA%B4%91%EC%97%AD%EC%8B%9C.geojson')
c = r.content
busan_geo = json.loads(c)

## 2 전처리 작업

### 2.1 데이터 전처리 후 결합
- (지역구)_요일_시간대별 방문자 집중율 * (지역구)_방문자 수
- 각 지역구별 시간대별 방문자 수 추산하여 하나의 데이터프레임으로 결합

In [3]:
import os

path = "./"
file_list = os.listdir(path)
csv_list = [file for file in file_list if file.endswith(".csv")]
csv_list

['강서구_방문자 수.csv',
 '강서구_요일_시간대 별 방문자 집중율.csv',
 '금정구_방문자 수.csv',
 '금정구_요일_시간대 별 방문자 집중율.csv',
 '기장군_방문자 수.csv',
 '기장군_요일_시간대 별 방문자 집중율.csv',
 '남구_방문자 수.csv',
 '남구_요일_시간대 별 방문자 집중율.csv',
 '동구_방문자 수.csv',
 '동구_시간대 별 방문자 집중율.csv',
 '동래구_방문자 수.csv',
 '동래구_요일_시간대 별 방문자 집중율.csv',
 '부산진구_방문자 수.csv',
 '부산진구_요일_시간대 별 방문자 집중율.csv',
 '북구_방문자 수.csv',
 '북구_요일_시간대 별 방문자 집중율.csv',
 '사상구_방문자 수.csv',
 '사상구_요일_시간대 별 방문자 집중율.csv',
 '사하구_방문자 수.csv',
 '사하구_요일_시간대 별 방문자 집중율.csv',
 '서구_방문자 수.csv',
 '서구_요일_시간대 별 방문자 집중율.csv',
 '수영구_방문자 수.csv',
 '수영구_요일_시간대 별 방문자 집중율.csv',
 '연제구_방문자 수.csv',
 '연제구_요일_시간대 별 방문자 집중율.csv',
 '영도구_방문자 수.csv',
 '영도구_요일_시간대 별 방문자 집중율.csv',
 '중구_방문자 수.csv',
 '중구_요일_시간대 별 방문자 집중율.csv',
 '해운대구_방문자 수.csv',
 '해운대구_요일_시간대 별 방문자 집중율.csv']

In [30]:
visitor_csv = [csv for csv in csv_list if csv.split(".")[0].endswith("수")]
time_csv = [csv for csv in csv_list if csv not in visitor_csv]
gu_list = [csv.split("_")[0] for csv in time_csv]

In [31]:
print(len(visitor_csv), len(time_csv))
print(gu_list)

16 16
['강서구', '금정구', '기장군', '남구', '동구', '동래구', '부산진구', '북구', '사상구', '사하구', '서구', '수영구', '연제구', '영도구', '중구', '해운대구']


In [32]:
pd.read_csv("연제구_요일_시간대 별 방문자 집중율.csv", encoding = "cp949")

요일  방문 시간대  방문자 집중률
0   일요일  00~06시    2.400
1   일요일  06~11시    2.600
2   일요일  11~14시    2.600
3   일요일  14~18시    3.300
4   일요일  18~21시    1.900
5   일요일  21~24시    1.200
6   월요일  00~06시    1.700
7   월요일  06~11시    2.700
8   월요일  11~14시    2.300
9   월요일  14~18시    3.100
10  월요일  18~21시    1.900
11  월요일  21~24시    1.200
12  화요일  00~06시    1.600
13  화요일  06~11시    2.700
14  화요일  11~14시    2.400
15  화요일  14~18시    3.200
16  화요일  18~21시    2.000
17  화요일  21~24시    1.300
18  수요일  00~06시    1.600
19  수요일  06~11시    2.700
20  수요일  11~14시    2.400
21  수요일  14~18시    3.200
22  수요일  18~21시    2.100
23  수요일  21~24시    1.400
24  목요일  00~06시    1.600
25  목요일  06~11시    2.700
26  목요일  11~14시    2.300
27  목요일  14~18시    3.100
28  목요일  18~21시    2.100
29  목요일  21~24시    1.400
30  금요일  00~06시    1.700
31  금요일  06~11시    2.900
32  금요일  11~14시    2.500
33  금요일  14~18시    3.400
34  금요일  18~21시    2.400
35  금요일  21~24시    1.800
36  토요일  00~06시    2.400
37  토요일  06~11시    3.100
38  토요일  11~14시    3.300
39  토요일  14~18시    4.500
40  토요일  18~21시    3.200
41  토요일  21~24시    2.200

In [25]:
df_visitor = pd.DataFrame()

for gu, csv in zip(gu_list, visitor_csv):
    df = pd.read_csv(csv, encoding = "cp949")
    df["지역구"] = gu
    df_visitor = df_visitor.append(df)

df_visitor

기준연월        방문자수   지역구
0   202201 2836937.000   강서구
1   202202 2498954.000   강서구
2   202203 2863433.000   강서구
3   202204 3318821.000   강서구
4   202205 3277041.000   강서구
..     ...         ...   ...
7   202208 6428823.000  해운대구
8   202209 5351563.000  해운대구
9   202210 5799430.000  해운대구
10  202211 5255393.000  해운대구
11  202212 5797922.000  해운대구

[192 rows x 3 columns]

In [33]:
df_time = pd.DataFrame()

for gu, csv in zip(gu_list, time_csv):
    df = pd.read_csv(csv, encoding = "cp949")
    df["지역구"] = gu
    df_time = df_time.append(df)

df_time       

요일  방문 시간대  방문자 집중률   지역구
0   일요일  00~06시    1.300   강서구
1   일요일  06~11시    3.100   강서구
2   일요일  11~14시    3.400   강서구
3   일요일  14~18시    4.600   강서구
4   일요일  18~21시    2.200   강서구
..  ...     ...      ...   ...
37  토요일  06~11시    3.200  해운대구
38  토요일  11~14시    3.400  해운대구
39  토요일  14~18시    5.200  해운대구
40  토요일  18~21시    3.200  해운대구
41  토요일  21~24시    2.200  해운대구

[672 rows x 4 columns]

In [48]:
df_202212 = df_visitor.loc[df_visitor["기준연월"] == 202212, ["지역구", "방문자수"]].reset_index(drop = True)

In [65]:
df_time["방문자 집중률"] = df_time["방문자 집중률"] / 100

In [66]:
df_visitor_time = df_time.join(df_202212.set_index("지역구"), on = "지역구")

In [67]:
df_visitor_time["시간별방문자수"] = df_visitor_time["방문자 집중률"] * df_visitor_time["방문자수"]

In [98]:
df_visitor_time.to_csv("부산시_지역별_시간대별_방문자수.csv")

In [100]:
df_visitor_time

요일  방문 시간대  방문자 집중률   지역구        방문자수    시간별방문자수
0   일요일  00~06시    0.013   강서구 3079993.000  40039.909
1   일요일  06~11시    0.031   강서구 3079993.000  95479.783
2   일요일  11~14시    0.034   강서구 3079993.000 104719.762
3   일요일  14~18시    0.046   강서구 3079993.000 141679.678
4   일요일  18~21시    0.022   강서구 3079993.000  67759.846
..  ...     ...      ...   ...         ...        ...
37  토요일  06~11시    0.032  해운대구 5797922.000 185533.504
38  토요일  11~14시    0.034  해운대구 5797922.000 197129.348
39  토요일  14~18시    0.052  해운대구 5797922.000 301491.944
40  토요일  18~21시    0.032  해운대구 5797922.000 185533.504
41  토요일  21~24시    0.022  해운대구 5797922.000 127554.284

[672 rows x 6 columns]

In [88]:
df_example = df_visitor_time.groupby("지역구").mean().reset_index()

In [99]:
# busan_geo

In [96]:
m = folium.Map(
    location=[35.137922, 129.055628],
    zoom_start=11, 
    tiles='OpenStreetMap',
    zoom_control = True
)

folium.GeoJson(
    busan_geo,
    name='지역명',
).add_to(m)

folium.Choropleth(
            geo_data= busan_geo,
            data=df_example,
            columns = ["지역구", "시간별방문자수"],
            fill_color='RdBu_r',
            line_color="Black", 
            fill_opacity=0.8,
            line_opacity=1.0,
            bins = 10,        
            key_on='properties.sggnm',
            legend_name='지역별 방문자수').add_to(m) 

m